In [26]:
import datetime
import os
from pathlib import Path

import numpy as np
import pandas as pd
import scipy
import xarray as xr
from datatree import DataTree


def extinction_learning(datatree: DataTree) -> xr.Dataset:
    """Produce extinction learning results."""
    return xr.DataArray(data=np.ndarray(shape=(3)), dims=("Trial"))


def date_from_filename(filename: str) -> datetime.datetime:
    """Convert filename to datetime object.

    Args:
    ----
        filename (str): The filename to convert.

    Returns:
    -------
        datetime.datetime: The converted datetime object.
    """
    return datetime.datetime.strptime(
        filename[12:-4],
        "%d_%m_%Y_%H_%M",
    ).replace(tzinfo=datetime.UTC)


def session_attrs(filepath: Path) -> dict:
    """Extract session attributes from a file.

    Args:
    ----
        filepath (pathlib.Path): The path to the file.

    Returns:
    -------
        dict: The extracted session attributes.
    """
    c = scipy.io.loadmat(
        filepath,
        squeeze_me=True,
    )["c"]

    return {
        field_name: data
        for field_name, data in {
            field_name: c.item()[i] for i, field_name in enumerate(c.dtype.names)
        }.items()
        if not isinstance(data, np.ndarray)
    }


def dt_index_from_data_dir(data_dir: Path) -> pd.DatetimeIndex:
    """Create a pandas DatetimeIndex from the files in the specified data directory.

    Parameters
    ----------
        data_dir (Path): The path to the directory containing the data files.

    Returns
    -------
        pd.DatetimeIndex: A pandas DatetimeIndex object representing the timestamps
        extracted from the file names.
    """
    return pd.Index(
        pd.to_datetime(
            pd.DataFrame.from_records(
                [path.stem.split("_") for path in data_dir.glob("*.mat")],
                columns=["Experiment Label", "day", "month", "year", "hour", "minute"],
            )[["day", "month", "year", "hour", "minute"]],
        ),
        name="datetime",
    )


def sessions(data_dir: str) -> pd.DataFrame:
    """Retrieve session data as a DataFrame."""
    filenames = Path(os.environ["XDG_DATA_HOME"]) / data_dir
    filepaths = filenames.glob("*.mat")
    return pd.DataFrame.from_records(
        [session_attrs(filepath) for filepath in filepaths],
        index=dt_index_from_data_dir(filenames),
    )

In [27]:
sessions("BFINAC_VNS")

learningfracgenerate  targetAcquisitionRequired  \
datetime                                                               
2018-10-24 16:01:00                   1.0                        0.1   
2018-12-20 16:57:00                   0.0                        0.1   
2019-01-22 14:41:00                   1.0                        0.1   
2019-01-15 14:28:00                   1.0                        0.1   
2018-11-20 15:28:00                   1.0                        0.1   
...                                   ...                        ...   
2019-01-17 14:54:00                   1.0                        0.1   
2018-12-20 15:55:00                   0.0                        0.1   
2019-01-16 14:29:00                   1.0                        0.1   
2018-12-21 14:56:00                   0.0                        0.1   
2019-01-30 16:38:00                   1.0                        0.1   

                     fixOverlap  probblockonly  minFixDur  maxFixDur  \
datetime                                                               
2018-10-24 16:01:00        0.35              0          1          1   
2018-12-20 16:57:00        0.00              0          1          1   
2019-01-22 14:41:00        0.50              0          1          1   
2019-01-15 14:28:00        0.50              0          1          1   
2018-11-20 15:28:00        0.35              0          1          1   
...                         ...            ...        ...        ...   
2019-01-17 14:54:00        0.50              0          1          1   
2018-12-20 15:55:00        0.00              0          1          1   
2019-01-16 14:29:00        0.50              0          1          1   
2018-12-21 14:56:00        0.00              0          1          1   
2019-01-30 16:38:00        0.50              0          1          1   

                     freeRewardProbability  fp1WindH  fp1WindW  maxFixWait  \
datetime                                                                     
2018-10-24 16:01:00                   0.01         5         5           5   
2018-12-20 16:57:00                   0.01         5         5           5   
2019-01-22 14:41:00                   0.01         4         4           5   
2019-01-15 14:28:00                   0.01         4         4           5   
2018-11-20 15:28:00                   0.01         5         5           5   
...                                    ...       ...       ...         ...   
2019-01-17 14:54:00                   0.01         4         4           5   
2018-12-20 15:55:00                   0.01         5         5           5   
2019-01-16 14:29:00                   0.01         4         4           5   
2018-12-21 14:56:00                   0.01         5         5           5   
2019-01-30 16:38:00                   0.01         4         4           5   

                     ...  freelookamp  ITItime  outcomedel  chosenwindow  \
datetime             ...                                                   
2018-10-24 16:01:00  ...           10    1.439         1.0             0   
2018-12-20 16:57:00  ...           10    1.325         1.0             0   
2019-01-22 14:41:00  ...           10    1.303         NaN             0   
2019-01-15 14:28:00  ...           10    1.263         1.0             0   
2018-11-20 15:28:00  ...           10    1.242         1.0             0   
...                  ...          ...      ...         ...           ...   
2019-01-17 14:54:00  ...           10    1.444         NaN             0   
2018-12-20 15:55:00  ...           10    1.324         1.0             0   
2019-01-16 14:29:00  ...           10    1.456         NaN             0   
2018-12-21 14:56:00  ...           10    1.317         1.0             0   
2019-01-30 16:38:00  ...           10    1.404         1.0             0   

                     monkeynotinitiated  loopCountOfTargetOn  \
datetime                                                       
2018-10-24 16:0

In [28]:
sessions_xr = _.to_xarray()

In [29]:
sessions_xr

<xarray.Dataset>
Dimensions:                      (datetime: 76)
Coordinates:
  * datetime                     (datetime) datetime64[ns] 2018-10-24T16:01:0...
Data variables: (12/101)
    learningfracgenerate         (datetime) float64 1.0 0.0 1.0 ... 1.0 0.0 1.0
    targetAcquisitionRequired    (datetime) float64 0.1 0.1 0.1 ... 0.1 0.1 0.1
    fixOverlap                   (datetime) float64 0.35 0.0 0.5 ... 0.5 0.0 0.5
    probblockonly                (datetime) int64 0 0 0 0 0 0 0 ... 0 0 0 0 0 0
    minFixDur                    (datetime) int64 1 1 1 1 1 1 1 ... 1 1 1 1 1 1
    maxFixDur                    (datetime) int64 1 1 1 1 1 1 1 ... 1 1 1 1 1 1
    ...                           ...
    monkeynotinitiated           (datetime) int64 0 0 0 0 0 0 0 ... 0 0 0 0 0 0
    loopCountOfTargetOn          (datetime) float64 708.0 860.0 ... 1.296e+03
    loopCountOfTargetOff         (datetime) float64 nan nan nan ... nan nan nan
    setWindow                    (datetime) int64 0 0 0 0 0 0 0 ... 0 0 0 0 0 0
    PlotsWanted                  (datetime) float64 nan 4.0 4.0 ... 4.0 4.0 4.0
    continueplot                 (datetime) float64 nan 1.0 1.0 ... 1.0 1.0 1.0

In [4]:
sessions("BFINAC_VNS")

FileNotFoundError: [Errno 2] No such file or directory: 'data/BFINAC_VNS/BFnovelinac_24_10_2018_16_01.mat'

In [2]:
date_array = [
    [int(num) for num in path.name[12:-4].split("_")]
    for path in Path("data/BFINAC_VNS").glob("*.mat")
]

session_index = pd.Index(
    sorted(
        [
            datetime(year, month, day, hour, minute)
            for day, month, year, hour, minute in date_array
        ],
    ),
)
session_index[0]

NameError: name 'pd' is not defined

In [1]:
session_index

NameError: name 'session_index' is not defined

In [32]:
import scipy

session_data = scipy.io.loadmat(
    "data/BFINAC_VNS/BFnovelinac_22_10_2018_15_55.mat",
    squeeze_me=True,
)
session_data.keys()

dict_keys(['__header__', '__version__', '__globals__', 'PDS', 'c', 's', '__function_workspace__'])

In [49]:
session_trials = pd.DataFrame(
    {
        field: pd.Series(session_data["PDS"][field].item(), name=field)
        for field in session_data["PDS"].dtype.names
        if field
        not in [
            "EyeJoy",
            "onlineEye",
            "onlineLickForce",
            "spikes",
            "sptimes",
            "samplesBlinkLogical",
            "img1",
            "imgfeedback",
        ]
    },
).set_index("trialnumber")
session_trials

timeFocused  acquisitionTime stableWindowByTrial  \
trialnumber                                                     
1                    NaN              NaN                 NaN   
2                    NaN              NaN                 NaN   
3                    NaN              NaN                 NaN   
4                    NaN              NaN                 NaN   
5                    NaN              NaN                 NaN   
...                  ...              ...                 ...   
229                  NaN              NaN                 NaN   
230                  NaN              NaN                 NaN   
231                  NaN              NaN                 NaN   
232                  NaN              NaN                 NaN   
233                  NaN              NaN                 NaN   

            meanPrestimulusDialation  fixOverlap  targetacquisitionthreshold  \
trialnumber                                                                    
1                                NaN        0.35                         0.1   
2                                NaN        0.35                         NaN   
3                                NaN         NaN                         NaN   
4                                NaN        0.35                         NaN   
5                                NaN        0.35                         NaN   
...                              ...         ...                         ...   
229                              NaN         NaN                         NaN   
230                              NaN        0.35                         NaN   
231                              NaN        0.35                         NaN   
232                              NaN         NaN                         NaN   
233                              NaN        0.35                         NaN   

             fractals  targetAcquisitionBegin  targetAcquisitionFirst  \
trialnumber                                                             
1                6203            1.140506e+07            1.140505e+07   
2                6212                     NaN                     NaN   
3                6212                     NaN                     NaN   
4                6212                     NaN                     NaN   
5                6212            1.140508e+07            1.140507e+07   
...               ...                     ...                     ...   
229              6212                     NaN                     NaN   
230              6212            1.140658e+07            1.140657e+07   
231              6304            1.140658e+07            1.140658e+07   
232              6202                     NaN                     NaN   
233              6202            1.140660e+07            1.140659e+07   

             targAngle  ...  timeoutcome  repeatflag  monkeynotinitiated  \
trialnumber             ...                                                
1                    0  ...     4.424960           0                   0   
2                  180  ...          NaN           1                   0   
3                  180  ...          NaN           1                   0   
4                  180  ...          NaN           1                   0   
5                  180  ...     4.269805           0                   0   
...                ...  ...          ...         ...                 ...   
229                  0  ...          NaN           1                   0   
230                  0  ...     4.383807           0                   0   
231                180  ...     4.261978           0                   0   
232                180  ...          NaN           1                   0   
233                180  ...     4.260904           0                   0   

             FEEDbacktime  blinkthreshold  blinkTimeAllowed  trueCS_dur  \
trialnumber                                                               
1                2.011912            

In [55]:
eyejoy = pd.DataFrame.from_records(session_data["PDS"]["EyeJoy"].item()).explode(
    [0, 1, 2, 3, 4],
)
eyejoy

0         1         2         3            4
0    3.039551  2.366028 -2.001953  1.730957  4559.583132
0    3.043823  2.366333 -2.001343  1.733704  4559.584132
0    3.041992  2.369995 -2.001953   1.73584  4559.585132
0    3.035278  2.367249 -1.998291  1.739807  4559.586132
0    3.031311  2.366943 -2.000122  1.723938  4559.587132
..        ...       ...       ...       ...          ...
232       0.0       0.0       0.0       0.0          0.0
232       0.0       0.0       0.0       0.0          0.0
232       0.0       0.0       0.0       0.0          0.0
232       0.0       0.0       0.0       0.0          0.0
232       0.0       0.0       0.0       0.0          0.0

[2330000 rows x 5 columns]

In [68]:
session_data["PDS"]["EyeJoy"].item()

array([array([[ 3.03955078e+00,  3.04382324e+00,  3.04199219e+00, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [ 2.36602783e+00,  2.36633301e+00,  2.36999512e+00, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [-2.00195312e+00, -2.00134277e+00, -2.00195312e+00, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [ 1.73095703e+00,  1.73370361e+00,  1.73583984e+00, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [ 4.55958313e+03,  4.55958413e+03,  4.55958513e+03, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00]])   ,
       array([[ 2.74658203e-03,  1.09863281e-02,  1.73950195e-02, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [ 1.78161621e+00,  1.75262451e+00,  1.70867920e+00, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [-2.61322021e+0

In [79]:
online_eye = session_data["PDS"]["onlineEye"].item()

pd.concat({i: pd.DataFrame(online_eye[i]) for i in range(len(online_eye))}).xs(0)

0          1         2             3
0     24.372559  18.764648 -1.993408  1.140505e+07
1     24.274902  18.764648 -1.973267  1.140505e+07
2     24.274902  18.764648 -1.973267  1.140505e+07
3     24.274902  18.798828 -1.978455  1.140505e+07
4     24.274902  18.798828 -1.978455  1.140505e+07
...         ...        ...       ...           ...
3384   7.292480  35.930176 -0.867310  1.140506e+07
3385   7.292480  35.930176 -0.867310  1.140506e+07
3386   7.021484  36.166992 -0.866699  1.140506e+07
3387   7.021484  36.166992 -0.866699  1.140506e+07
3388   6.638184  36.882324 -0.853271  1.140506e+07

[3389 rows x 4 columns]

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
from matplotlib import animation

fig, ax = plt.subplots()
ax.set_xlim([0, 10])

scat = ax.scatter(1, 0)
x = np.linspace(0, 10)


def animate(i):
    scat.set_offsets((x[i], 0))
    return (scat,)


ani = animation.FuncAnimation(fig, animate, repeat=True, frames=len(x) - 1, interval=50)

# To save the animation using Pillow as a gif
# writer = animation.PillowWriter(fps=15,
#                                 metadata=dict(artist='Me'),
#                                 bitrate=1800)
# ani.save('scatter.gif', writer=writer)

plt.show()

In [61]:
session_data["c"].dtype.names

('targetAcquisitionRequired',
 'fixOverlap',
 'probblockonly',
 'minFixDur',
 'maxFixDur',
 'freeRewardProbability',
 'fp1WindH',
 'fp1WindW',
 'maxFixWait',
 'targFixDurReq',
 'tp1WindH',
 'tp1WindW',
 'choicemax',
 'targetdur',
 'fpX',
 'fpY',
 'overlapMin',
 'overlapMax',
 'minLatency',
 'maxLatency',
 'minTargFix',
 'maxTargFix',
 'rewardDur',
 'vFiltLength',
 'passEye',
 'vThresh',
 'postChoiceOnScreenTime',
 'output_prefix',
 'protocol_title',
 'TargAmp',
 'numTargAngles',
 'rewardDelay',
 'j',
 'trialnumber',
 'EyePtR',
 'fixdotW',
 'fixwinW',
 'cursorW',
 'framerate',
 'useDataPixxBool',
 'quit',
 'screen_number',
 'minTargAmp',
 'maxTargAmp',
 'freelookingset',
 'rasterLineCount',
 'runflag',
 'viewdist',
 'screenhpix',
 'screenh',
 'preTrialIti',
 'repeatflag',
 'previousTrialRepeated',
 'goodtrial',
 'codes',
 'fixreq',
 'freq',
 'rightFreq',
 'wrongFreq',
 'nTF',
 'lrMode',
 'wrongbuffadd',
 'wrongtone',
 'righttone',
 'noisetone',
 'bgRGB',
 'mutedGreen',
 'colorone',
 'co

In [62]:
session_data["s"].dtype.names

('TrialNumber',
 'TrialType',
 'TrialType1',
 'blocknumber',
 'successfulTrials',
 'choiceblocksCompleted',
 'choicetrialsCompleted',
 'targXY',
 'escapeXY',
 'fixDur',
 'RewardTime',
 'fixXY',
 'EyeX',
 'EyeY')

In [42]:
time_focused = pd.Series(session_data["PDS"]["timeFocused"].item(), name="timeFocused")
time_focused

0     NaN
1     NaN
2     NaN
3     NaN
4     NaN
       ..
228   NaN
229   NaN
230   NaN
231   NaN
232   NaN
Name: timeFocused, Length: 233, dtype: float64

In [43]:
acquisition_time = pd.Series(
    session_data["PDS"]["acquisitionTime"].item(),
    name="acquisitionTime",
)
acquisition_time

0     NaN
1     NaN
2     NaN
3     NaN
4     NaN
       ..
228   NaN
229   NaN
230   NaN
231   NaN
232   NaN
Name: acquisitionTime, Length: 233, dtype: float64

In [62]:
s = data["s"]
len(s.item())

14

In [63]:
s.dtype

dtype([('TrialNumber', 'O'), ('TrialType', 'O'), ('TrialType1', 'O'), ('blocknumber', 'O'), ('successfulTrials', 'O'), ('choiceblocksCompleted', 'O'), ('choicetrialsCompleted', 'O'), ('targXY', 'O'), ('escapeXY', 'O'), ('fixDur', 'O'), ('RewardTime', 'O'), ('fixXY', 'O'), ('EyeX', 'O'), ('EyeY', 'O')])

In [68]:
{field_name: s.item()[i] for i, field_name in enumerate(s.dtype.names)}

{'TrialNumber': 508,
 'TrialType': 6101,
 'TrialType1': 0,
 'blocknumber': 7,
 'successfulTrials': 401,
 'choiceblocksCompleted': 0,
 'choicetrialsCompleted': -1,
 'targXY': array([-15,   0], dtype=int16),
 'escapeXY': array([ 0, 15], dtype=uint8),
 'fixDur': 0.6,
 'RewardTime': 0.36192,
 'fixXY': array([0, 0], dtype=uint8),
 'EyeX': -397,
 'EyeY': -33}

In [69]:
element_fields = (
    "learningfracgenerate",
    "targetAcquisitionRequired",
    "fixOverlap",
    "minFixDur",
    "maxFixDur",
    "freeRewardProbability",
    "fp1WindH",
    "fp1WindW",
    "choicemax",
    "targetdur",
    "fpX",
    "fpY",
    "overlapMin",
    "overlapMax",
)

{'learningfracgenerate': 1,
 'targetAcquisitionRequired': 0.1,
 'fixOverlap': 0.5,
 'probblockonly': 0,
 'minFixDur': 1,
 'maxFixDur': 1,
 'freeRewardProbability': 0.01,
 'fp1WindH': 4,
 'fp1WindW': 4,
 'maxFixWait': 5,
 'targFixDurReq': 0.75,
 'tp1WindH': 5,
 'tp1WindW': 5,
 'choicemax': 7,
 'targetdur': 3,
 'fpX': 0,
 'fpY': 0,
 'overlapMin': 0,
 'overlapMax': 0,
 'minLatency': 0,
 'maxLatency': 0,
 'minTargFix': 0,
 'maxTargFix': 0,
 'rewardDur': 0.36192,
 'vFiltLength': 5,
 'passEye': 0,
 'vThresh': 25,
 'postChoiceOnScreenTime': 1,
 'output_prefix': 'BFnovelinac',
 'protocol_title': 'BFnovelinac',
 'TargAmp': 15,
 'numTargAngles': 8,
 'rewardDelay': 0,
 'j': 508,
 'trialnumber': 1,
 'EyePtR': 3,
 'fixdotW': 8,
 'fixwinW': 2,
 'cursorW': 6,
 'framerate': 100,
 'useDataPixxBool': 1,
 'quit': 0,
 'screen_number': 1,
 'minTargAmp': 15,
 'maxTargAmp': 15,
 'freelookingset': 6000,
 'rasterLineCount': array([0, 0, 0, 0, 0, 0], dtype=uint8),
 'runflag': 0,
 'viewdist': 410,
 'screenhpix':

learningfracgenerate            1
targetAcquisitionRequired     0.1
fixOverlap                    0.5
probblockonly                   0
minFixDur                       1
                             ... 
chosenwindow                    0
monkeynotinitiated              0
loopCountOfTargetOn          1255
loopCountOfTargetOff          NaN
setWindow                       0
Length: 101, dtype: object

In [75]:
c_data_subarrays = {
    field_name: data
    for field_name, data in c_data.items()
    if isinstance(data, np.ndarray)
}
c_data_subarrays.keys()

dict_keys(['rasterLineCount', 'codes', 'wrongtone', 'righttone', 'noisetone', 'bgRGB', 'mutedGreen', 'colorone', 'colortwo', 'humanColors', 'monkeyColors', 'humanCLUT', 'monkeyCLUT', 'combinedClut', 'screenRect', 'middleXY', 'onplotwin', 'onRastwin', 'plotax_looking', 'plotobj_looking', 'plotaxlookingTitle', 'ifFix', 'plotax_raster', 'plotax_rasterSum', 'plotobj_raster', 'plotobj_rasterSum', 'CsOnPlotLine', 'CsOffPlotLine', 'plotaxrasterTitle', 'targetWindowPdsVals', 'uniquefractallist', 'img1_', 'img3_', 'im1', 'im2', 'im3', 'possibleanglesfreelook', 'blinkLogicalSamples', 'plottype'])

In [80]:
{field_name: data.shape for field_name, data in c_data_subarrays.items()}

{'rasterLineCount': (6,),
 'codes': (),
 'wrongtone': (4800,),
 'righttone': (4800,),
 'noisetone': (4800,),
 'bgRGB': (3,),
 'mutedGreen': (3,),
 'colorone': (3,),
 'colortwo': (3,),
 'humanColors': (10, 3),
 'monkeyColors': (10, 3),
 'humanCLUT': (256, 3),
 'monkeyCLUT': (256, 3),
 'combinedClut': (512, 3),
 'screenRect': (4,),
 'middleXY': (2,),
 'onplotwin': (1,),
 'onRastwin': (1,),
 'plotax_looking': (1,),
 'plotobj_looking': (1,),
 'plotaxlookingTitle': (1,),
 'ifFix': (4,),
 'plotax_raster': (1,),
 'plotax_rasterSum': (1,),
 'plotobj_raster': (1,),
 'plotobj_rasterSum': (1,),
 'CsOnPlotLine': (1,),
 'CsOffPlotLine': (1,),
 'plotaxrasterTitle': (1,),
 'targetWindowPdsVals': (),
 'uniquefractallist': (6,),
 'img1_': (100, 100, 3),
 'img3_': (100, 100, 3),
 'im1': (100, 100, 3),
 'im2': (0,),
 'im3': (100, 100, 3),
 'possibleanglesfreelook': (4,),
 'blinkLogicalSamples': (6668,),
 'plottype': (508,)}

In [53]:
pd.Series(c.item()[4], name=c.dtype.names[4])

0    1
Name: minFixDur, dtype: int64

In [60]:
{field_name: c.item()[i] for i, field_name in enumerate(c.dtype.names)}

{'learningfracgenerate': 1,
 'targetAcquisitionRequired': 0.1,
 'fixOverlap': 0.5,
 'probblockonly': 0,
 'minFixDur': 1,
 'maxFixDur': 1,
 'freeRewardProbability': 0.01,
 'fp1WindH': 4,
 'fp1WindW': 4,
 'maxFixWait': 5,
 'targFixDurReq': 0.75,
 'tp1WindH': 5,
 'tp1WindW': 5,
 'choicemax': 7,
 'targetdur': 3,
 'fpX': 0,
 'fpY': 0,
 'overlapMin': 0,
 'overlapMax': 0,
 'minLatency': 0,
 'maxLatency': 0,
 'minTargFix': 0,
 'maxTargFix': 0,
 'rewardDur': 0.36192,
 'vFiltLength': 5,
 'passEye': 0,
 'vThresh': 25,
 'postChoiceOnScreenTime': 1,
 'output_prefix': 'BFnovelinac',
 'protocol_title': 'BFnovelinac',
 'TargAmp': 15,
 'numTargAngles': 8,
 'rewardDelay': 0,
 'j': 508,
 'trialnumber': 1,
 'EyePtR': 3,
 'fixdotW': 8,
 'fixwinW': 2,
 'cursorW': 6,
 'framerate': 100,
 'useDataPixxBool': 1,
 'quit': 0,
 'screen_number': 1,
 'minTargAmp': 15,
 'maxTargAmp': 15,
 'freelookingset': 6000,
 'rasterLineCount': array([0, 0, 0, 0, 0, 0], dtype=uint8),
 'runflag': 0,
 'viewdist': 410,
 'screenhpix':

In [40]:
{field_name: c.item()[i] for i, field_name in enumerate(c)}

array((508, 6101, 0, 7, 401, 0, -1, array([-15,   0], dtype=int16), array([ 0, 15], dtype=uint8), 0.6, 0.36192, array([0, 0], dtype=uint8), -397, -33),
      dtype=[('TrialNumber', 'O'), ('TrialType', 'O'), ('TrialType1', 'O'), ('blocknumber', 'O'), ('successfulTrials', 'O'), ('choiceblocksCompleted', 'O'), ('choicetrialsCompleted', 'O'), ('targXY', 'O'), ('escapeXY', 'O'), ('fixDur', 'O'), ('RewardTime', 'O'), ('fixXY', 'O'), ('EyeX', 'O'), ('EyeY', 'O')])

In [30]:
pds = data["PDS"]
eyejoy = pds["EyeJoy"].item()
len(eyejoy)

508

In [32]:
eyejoy

array([array([[ 4.97894287e+00,  4.98138428e+00,  4.98229980e+00, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [ 3.05114746e+00,  3.05053711e+00,  3.04931641e+00, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [-2.01446533e+00, -2.02423096e+00, -2.02423096e+00, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [ 1.80969238e+00,  1.81823730e+00,  1.80908203e+00, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [ 2.12985141e+04,  2.12985151e+04,  2.12985161e+04, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00]])   ,
       array([[ 3.69262695e-02,  3.90625000e-02,  4.11987305e-02, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [-2.81066895e-01, -2.81066895e-01, -2.84729004e-01, ...,
                0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
              [-2.07153320e+0

In [33]:
pds["onlineEye"].item()[0].shape

(6461, 4)

In [34]:
pds["onlineLickForce"].item()[0].shape

(6461, 2)

In [38]:
pds["samplesBlinkLogical"].item()[0]

array([0, 0, 0, ..., 0, 0, 0], dtype=uint8)

In [17]:
sub_arrays = (
    "EyeJoy",
    "onlineEye",
    "onlineLickForce",
    "samplesBlinkLogical",
    "img1",
    "imgfeedback",
    "spikes",
    "sptimes",
)

sparse_arrays = (
    "targetAcquisitionBegin",
    "targetAcquisitionFirst",
    "FEEDbacktime",
    "timeoutcome",
    "outcomedel",
    "ITIeventtime",
)

session_columns = (
    "targetacquisitionthreshold",
    "ITI_dur",
)

homogenous_arrays = (
    "targAmp",
    "fixreq",
    "windowchosen",
    "blinkthreshold",
    "blinkTimeAllowed",
    "trueCS_dur",
    "rewardduration",
)

trial_data = (
    pd.DataFrame(
        [
            pd.Series(pds.item()[i], name=field_name)
            for i, field_name in enumerate(pds.dtype.names)
            if field_name
            not in sub_arrays + sparse_arrays + session_columns + homogenous_arrays
        ],
    )
    .T.dropna(axis=1, how="all")
    .set_index("trialnumber")
)
trial_data

fixOverlap  fractals  targAngle  goodtrial  datapixxtime  \
trialnumber                                                             
1.0                 0.5    6212.0        0.0        1.0  21298.512505   
2.0                 0.5    6202.0        0.0        1.0  21308.260766   
3.0                 0.5    6302.0        0.0        1.0  21316.614368   
4.0                 0.5    6212.0      180.0        1.0  21326.137578   
5.0                 0.5    6202.0      180.0        1.0  21334.392459   
...                 ...       ...        ...        ...           ...   
504.0               0.5    6202.0      180.0        0.0  25009.668284   
505.0               NaN    6202.0      180.0        0.0  25013.591259   
506.0               0.5    6202.0      180.0        1.0  25016.411008   
507.0               0.5    6312.0        0.0        1.0  25023.562894   
508.0               0.5    6101.0      180.0        0.0  25031.883016   

             trialstarttime  timefpon  timefpoff  timetargeton  \
trialnumber                                                      
1.0            7.000005e+06  0.758113   2.041627      1.541559   
2.0            7.000014e+06  0.760564   2.027416      1.519004   
3.0            7.000023e+06  0.757499   1.866344      1.365954   
4.0            7.000032e+06  0.760028   1.868525      1.368451   
5.0            7.000040e+06  0.764097   1.872531      1.372509   
...                     ...       ...        ...           ...   
504.0          7.003716e+06  0.764094  -1.000000      1.672558   
505.0          7.003720e+06  0.758053  -1.000000           NaN   
506.0          7.003723e+06  0.763456   1.871972      1.371927   
507.0          7.003730e+06  0.762227   1.870734      1.370639   
508.0          7.003738e+06  0.759416  -1.000000      1.517771   

             loopCountOfTargetOn  timetargetoff  feedid  TrialTypeSave  \
trialnumber                                                              
1.0                       1211.0       4.533639  6212.0         6112.0   
2.0                       1245.0       4.519422  6202.0         6102.0   
3.0                       1142.0       4.366287  6302.0         6102.0   
4.0                       1138.0       4.368879  6212.0         6112.0   
5.0                       1131.0       4.372937  6202.0         6102.0   
...                          ...            ...     ...            ...   
504.0                     1405.0            NaN  6202.0         6102.0   
505.0                        NaN            NaN  6202.0         6102.0   
506.0                     1157.0       4.372392  6202.0         6102.0   
507.0                     1142.0       4.371070  6312.0         6112.0   
508.0                     1255.0            NaN  6101.0         6101.0   

             timefpabort  repeatflag  monkeynotinitiated  freeoutcometype  \
trialnumber                                                                 
1.0             0.000000         0.0                 0.0              1.0   
2.0             0.000000         0.0                 0.0             34.0   
3.0             0.000000         0.0                 0.0              1.0   
4.0             0.000000         0.0                 0.0              1.0   
5.0             0.000000         0.0                 0.0              1.0   
...                  ...         ...                 ...              ...   
504.0           2.155961         1.0                 0.0             34.0   
505.0           1.074773         1.0                 0.0             34.0   
506.0           0.000000         0.0                 0.0             34.0   
507.0           0.000000         0.0                 0.0              1.0   
508.0           2.009593         1.0                 0.0              1.0   

             setupITI  
trialnumber            
1.0               1.0  
2.0               0.0  
3.0               1.0  
4.0               0.0  
5.0               0.0  
...               ...  
504.0             0.0  
505.0             0.0  

In [60]:
session_data = {
    field_name: trial_data[field_name].iloc[0]
    for field_name in trial_data.columns
    if all(pd.isna(trial_data[field_name].iloc[1:]))
}
session_data

{'targetacquisitionthreshold': 0.1, 'ITI_dur': 1.0}

In [79]:
trial_data = trial_data.drop(
    columns=[
        field_name
        for field_name, series in trial_data.items()
        if isinstance(series.iloc[0], np.ndarray)
        and all(len(element) == 0 for element in series)
    ],
)

In [106]:
sparse_data = {
    field_name: trial_data[field_name].dropna() for field_name in sparse_columns
}

KeyError: 'targetAcquisitionBegin'

In [16]:
trial_data["targAmp"].unique()

array([10.])

In [66]:
from datatree import DataTree

DataTree.from_dict({"PDS": xr.DataArray(data["PDS"])})

ValueError: unable to convert unnamed DataArray to a Dataset without providing an explicit name

In [73]:
import pandas as pd

pd.DataFrame(data["PDS"])

ValueError: 2

In [74]:
data["PDS"]

array([[(array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
                nan, nan, n